# **ANALISIS EXPLORATORIO DE DATOS - VENTAS DE COCHES USADOS**

Este conjunto de datos corresponde a anuncios de venta de vehículos. 
Los registros reflejan las características de los autos ofertados y los precios determinados por los vendedores, pero no representan ventas concretadas, ni precios finales.

El objetivo de este análisis es explorar cómo se distribuye la oferta en el mercado de automóviles usados en cuanto a precios, tipo, modelo, 
kilometraje(odómetro), año de fabricación y tracción. Estas características asociadas a los vehículos, serán la base para presentar la información de forma clara 
y útil en la página web del proyecto.

A continuación, visualizaremos gráficos para entender la distribución de precios, la relación entre el precio comparado tanto con el año del vehículo, como por el kilometraje. Finalmente, se analizarán gráficos de caja donde se observarán las diferencias del precio entre los diferentes tipos de autos y entre los modelos de carros más comunes, así como el impacto en el precio ofertado por los vendedores, cuando un vehículo cuenta o no con tracción.

## **1.DESCARGA DEL ARCHIVO Y LAS LIBRERIAS**

In [103]:
# Importar las librerías necesarias
import pandas as pd
import plotly.express as px

In [104]:
# Descargar el dataset
carros = pd.read_csv("../vehicles_us.csv")

## **2.ESTUDIO DE LOS DATOS**

In [105]:
# Revisión de la Información que contiene el Dataset
carros.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 51525 entries, 0 to 51524
Data columns (total 13 columns):
 #   Column        Non-Null Count  Dtype  
---  ------        --------------  -----  
 0   price         51525 non-null  int64  
 1   model_year    47906 non-null  float64
 2   model         51525 non-null  object 
 3   condition     51525 non-null  object 
 4   cylinders     46265 non-null  float64
 5   fuel          51525 non-null  object 
 6   odometer      43633 non-null  float64
 7   transmission  51525 non-null  object 
 8   type          51525 non-null  object 
 9   paint_color   42258 non-null  object 
 10  is_4wd        25572 non-null  float64
 11  date_posted   51525 non-null  object 
 12  days_listed   51525 non-null  int64  
dtypes: float64(4), int64(2), object(7)
memory usage: 5.1+ MB


In [106]:
# Despliegue del contenido de las columnas del dataset
carros.head()


price  model_year           model  condition  cylinders fuel  odometer  \
0   9400      2011.0          bmw x5       good        6.0  gas  145000.0   
1  25500         NaN      ford f-150       good        6.0  gas   88705.0   
2   5500      2013.0  hyundai sonata   like new        4.0  gas  110000.0   
3   1500      2003.0      ford f-150       fair        8.0  gas       NaN   
4  14900      2017.0    chrysler 200  excellent        4.0  gas   80903.0   

  transmission    type paint_color  is_4wd date_posted  days_listed  
0    automatic     SUV         NaN     1.0  23/06/2018           19  
1    automatic  pickup       white     1.0  19/10/2018           50  
2    automatic   sedan         red     NaN  07/02/2019           79  
3    automatic  pickup         NaN     NaN  22/03/2019            9  
4    automatic   sedan       black     NaN  02/04/2019           28

### *EXPLORACION DE VALORES DUPLICADOS*

In [107]:
# Revisar la existencia de valores duplicados
cp = carros.duplicated().sum()
print(f"La cantidad de valores duplicados es: {cp}")

La cantidad de valores duplicados es: 0


### *EXPLORACION Y TRATAMIENTO DE VALORES AUSENTES*

In [108]:
# Revisar la existencia de valores ausentes
carros.isna().sum()

price               0
model_year       3619
model               0
condition           0
cylinders        5260
fuel                0
odometer         7892
transmission        0
type                0
paint_color      9267
is_4wd          25953
date_posted         0
days_listed         0
dtype: int64

In [109]:
# Revisión de los valores únicos de la columna "is_4wd"
carros["is_4wd"].unique()

array([ 1., nan])

In [110]:
# Rellenar la columna "is_4wd" (referente a si el vehículo tiene tracción de 4 ruedas) 
# con un valor de cero y pasarla de float a int
carros["is_4wd"] = carros["is_4wd"].fillna(0).astype(int)

# Renombrar la columna "is_4wd" a "traccion" para una mejor comprensión
carros.rename(columns={"is_4wd": "traccion"}, inplace=True)



**COMENTARIO:**
Se rellenaron los valores ausentes de la columna "is_4wd" con ceros, ya que al observar que los únicos valores existentes eran 1.0 y NaN, se asumió que la ausencia de valor indica que el vehículo no cuenta con tracción en las cuatro ruedas. Por lo tanto, se rellenaron los valores nulos con 0 y la columna fue transformada a tipo entero (int), representando esta variable como booleana (1: sí tiene 4WD, 0: no tiene). También realice el cambio de nombre de la columna "is_4wd" por "traccion" para una mejor comprensión.

En cuanto a las columnas que presentan una gran cantidad de valores ausentes, como "model_year", "cylinders", "odometer" y "paint_color", se decidió mantener dichos valores como ausentes en esta etapa. Esto se debe a que eliminar las filas podría comprometer seriamente la integridad del conjunto de datos, dado que los valores faltantes representan entre el 7% y el 50% del total. El tratamiento específico de estos valores se decidirá más adelante, en función del análisis estadístico correspondiente.

### **ANALSIS Y CORRECCION EN LOS TIPOS DE DATOS DE LAS COLUMNAS**

**COMENTARIO INICIAL:**
 
Al realizar la visualización de las primeras 5 filas de datos del dataset, identifique las siguientes columnas a cambiar sus tipos de datos potencialmente:

1) El primer juego de columnas de pasar su tipo de float a int, son: "model_year", "cylinders" y "odometer".

2) Cambiar el tipo de datos de la columna "date_posted" de object a datetime.

Para validar la estructura de los tipos de datos, revisaré el resumen de valores únicos de cada columna, y en base a ello, tomaré la decisión de realizar la conversión en los tipos de datos referida.

In [111]:
# Revisión de los valores únicos de la columna "model_year"
carros["model_year"].unique()

array([2011.,   nan, 2013., 2003., 2017., 2014., 2015., 2012., 2008.,
       2018., 2009., 2010., 2007., 2004., 2005., 2001., 2006., 1966.,
       1994., 2019., 2000., 2016., 1993., 1999., 1997., 2002., 1981.,
       1995., 1996., 1975., 1998., 1985., 1977., 1987., 1974., 1990.,
       1992., 1991., 1972., 1967., 1988., 1969., 1989., 1978., 1965.,
       1979., 1968., 1986., 1980., 1964., 1963., 1984., 1982., 1973.,
       1970., 1955., 1971., 1976., 1983., 1954., 1962., 1948., 1960.,
       1908., 1961., 1936., 1949., 1958., 1929.])

In [112]:
# Revisión de los valores únicos de la columna "cylinders"
carros["cylinders"].unique()

array([ 6.,  4.,  8., nan,  5., 10.,  3., 12.])

In [113]:
# Revisión de los valores únicos de la columna "odometer"
carros["odometer"].unique()

array([145000.,  88705., 110000., ..., 121778., 181500., 139573.],
      shape=(17763,))

In [114]:
# Cambiar los tipos de datos de float a int de las columnas "model_year", "cylinders" y "odometer"
carros["model_year"] = carros["model_year"].astype("Int64")
carros["cylinders"] = carros["cylinders"].astype("Int64")
carros["odometer"] = carros["odometer"].astype("Int64")


In [115]:
# Cambiar el tipo de datos de object a datetime de la columna "date_posted"
carros["date_posted"] = pd.to_datetime(carros["date_posted"], format="%d/%m/%Y")

In [116]:
# Se verifica la conversión de los tipos de datos
carros.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 51525 entries, 0 to 51524
Data columns (total 13 columns):
 #   Column        Non-Null Count  Dtype         
---  ------        --------------  -----         
 0   price         51525 non-null  int64         
 1   model_year    47906 non-null  Int64         
 2   model         51525 non-null  object        
 3   condition     51525 non-null  object        
 4   cylinders     46265 non-null  Int64         
 5   fuel          51525 non-null  object        
 6   odometer      43633 non-null  Int64         
 7   transmission  51525 non-null  object        
 8   type          51525 non-null  object        
 9   paint_color   42258 non-null  object        
 10  traccion      51525 non-null  int64         
 11  date_posted   51525 non-null  datetime64[ns]
 12  days_listed   51525 non-null  int64         
dtypes: Int64(3), datetime64[ns](1), int64(3), object(6)
memory usage: 5.3+ MB


#### **CONCLUSION SOBRE MANEJO DE TIPO DE DATOS

El análisis de los valores únicos en las columnas mencionadas confirmó que sus valores deberían representarse como enteros (int), por lo que se corrigió su tipo de datos. En el caso de la columna "date_posted", al contener fechas, se convirtió al tipo datetime para facilitar operaciones de filtrado, ordenamiento y análisis temporal.



## **VISUALIZACION DE LOS DATOS CON GRAFICOS E HISTOGRAMAS**

In [117]:
# Histograma de distribución de precios en los anuncios de venta de vehículos usados
fig = px.histogram(carros, x="price", nbins=30, title="Distribución de precios de los vehículos en anuncios")
fig.update_layout(xaxis_title="Precio (USD)", yaxis_title="Cantidad de anuncios")
fig.show()


**COMENTARIO:**
Se observa que la mayoría de los anuncios se concentran en precios menores a $50,000, mientras que existe una minoría de vehículos con precios considerablemente más altos, lo cual puede incluir vehículos de lujo o datos atípicos que convendría analizar con mayor detalle posteriormente.


In [118]:
# Gráfico de dispersión que compara la relación entre el año y precio ofertado en los anuncios

# Se filtran los datos para quitar valores nulos en la columna 'model_year'
carros_filtrado_model_year = carros.dropna(subset=['model_year'])

# Se crea el gráfico
fig = px.scatter(carros_filtrado_model_year, 
                 x="model_year", 
                 y="price", 
                 trendline="ols",
                 title="Relación entre año y precio de los vehículos en los anuncios")

fig.update_layout(xaxis_title="Año del vehículo", 
                  yaxis_title="Precio (USD)")

fig.show()


**COMENTARIO:**
Los vehículos más nuevos tienden a tener precios más altos, aunque la relación no es fuerte. Existen muchos casos atípicos, como autos antiguos con precios elevados, lo que indica que otros factores además del año influyen significativamente en el precio.


In [119]:
# Gráfico de dispersión que compara la relación entre precio y kilometraje(odómetro)

# Se filtran los datos para eliminar valores nulos en la columna 'odometer'
carros_filtrado_odometer = carros.dropna(subset=['odometer'])

# Se crea el gráfico
fig = px.scatter(carros_filtrado_odometer,
                 x="odometer",
                 y="price",
                 trendline="ols",
                 title="Relación entre kilometraje y precio de los vehículos en los anuncios")

fig.update_layout(xaxis_title="Kilometraje (millas)",
                  yaxis_title="Precio (USD)")
fig.show()


**COMENTARIO:** Como era de esperarse, a mayor kilometraje, el precio de los vehículos tiende a ser más bajo. Sin embargo, se observa una dispersión considerable en los datos, lo cual indica que, aunque el kilometraje influye, no es el único factor determinante en el precio. Algunos vehículos con alto kilometraje presentan precios elevados, lo cual podría deberse a características como marca, estado, tipo de vehículo o año de fabricación.

In [125]:
# Diagrama de Caja de la distribución de precios por tipo de vehículo

carros_precio_filtrado = carros[carros["price"] < 100000]
fig = px.box(carros_precio_filtrado, x="type", y="price",
             title="Distribución de precios por tipo de vehículo")
fig.update_layout(xaxis_title="Tipo de vehículo", yaxis_title="Precio (USD)")
fig.show()


**COMENTARIO:** Se observa que algunos tipos de vehículos, como SUVs y pickups, suelen tener rangos de precio más altos comparados con autos compactos o sedanes.


In [121]:
# Diagrama de Caja de la distribución de precios de los 10 modelos de autos más comunes  

# Filtrar los top 10 modelos con más registros
top_10_modelos = carros['model'].value_counts().head(10).index
carros_top_10 = carros[carros['model'].isin(top_10_modelos)]

# Diagrama de caja del precio para los top 10 modelos
fig = px.box(carros_top_10, x="model", y="price", 
             title="Distribución de precios para los 10 modelos de vehículo más comunes")
fig.update_layout(xaxis_title="Modelo de vehículo", yaxis_title="Precio (USD)")
fig.show()



**COMENTARIO:** Entre los 10 modelos de vehículo más comunes, se observan diferencias notables en los rangos de precio. Por ejemplo, camionetas como la Ford F-150, RAM 2500 y las Chevrolet Silverado, suelen tener precios más altos y mayor dispersión, mientras que sedanes como el Toyota Camry o el Honda Accord tienden a tener precios más bajos y concentrados.


In [124]:
# Diagrama de Caja de la distribución de precios si el vehículo tiene tracción o no

# Reemplazar los valores de la columna "traccion" para una mejor comprensión
carros["traccion"] = carros["traccion"].replace({1: "Con Tracción", 0: "Sin Tracción"})

# Crear gráfico de caja
fig = px.box(carros, x="traccion", y="price",
             title="Distribución de precios por la presencia o ausencia de tracción 4x4")

fig.update_layout(xaxis_title="Tipo de tracción", yaxis_title="Precio (USD)")
fig.show()



**COMENTARIO:** Se observa que los vehículos que cuentan con tracción 4x4 tienden a tener precios más altos en comparación con aquellos que no la tienen. Esto es evidente tanto en los valores medianos como en el rango general de precios, lo cual puede atribuirse a que los autos 4x4 suelen estar asociados con pickups, SUVs o vehículos todoterreno, que por lo general tienen mayor equipamiento, tamaño y capacidades. Además, presentan más valores atípicos, lo que indica que algunos modelos específicos 4x4 alcanzan precios significativamente más altos.


## **4.CONCLUSION GENERAL DEL ANALISIS EXPLORATORIO DE DATOS**

El análisis exploratorio de los datos permitió identificar varias tendencias importantes en el mercado de vehículos. En primer lugar, se evidenció una correlación positiva entre el precio de los vehículos y características como el año del modelo, tipo de tracción (4x4) y modelo de vehículo. Los modelos más comunes, como pickups y SUVs, tienden a tener una distribución de precios más alta y más amplia en comparación con autos sedán o compactos.

Además, se observó que los vehículos con tracción 4x4 presentan precios notablemente mayores en promedio, lo cual puede estar relacionado con su uso especializado, mayor equipamiento o robustez. También se detectaron valores atípicos en varias categorías, lo que sugiere la presencia de vehículos con características especiales o ediciones premium.

En resumen, las variables más influyentes en el precio parecen estar asociadas con el tipo de vehículo, su tracción y la popularidad del modelo, lo que ofrece una base sólida para estudios posteriores o estrategias de precios.

